In [7]:
from PIL import Image
import imageio
import matplotlib.pyplot as plt
import numpy as np
import math
import cv2


#Function for zero padding
def getZeroPaddedImage(f, w):
    k_Size_m, k_size_n = w.shape; # get kernel Size
    m, n = f.size
    #print("Before Zero Padding", f.size)
    
    img_ZeroPad_Arr = np.pad(f, ((k_Size_m-1,k_Size_m-1), (k_size_n - 1, k_size_n - 1), (0, 0)), mode='constant', constant_values=0)
    img_ZeroPad = Image.fromarray(img_ZeroPad_Arr)
    #img_ZeroPad.save("E:\Avinash\GRAD\dis\ECE558-Project2\\" + imgName + "_ZeroPad.png")
    #print("After zero padding",img_ZeroPad.size)
    
    ######## Zero Padding Implementation from Scratch ###############
    
    #################################################################
    
    return img_ZeroPad

def getZeroPaddedImageGrayScale(f, w):
    
    k_Size_m, k_size_n = w.shape; # get kernel Size
    m, n = f.size
    #print("Before Zero Padding", f.size)
    
    img_ZeroPad_Arr = np.pad(f, ((k_Size_m-1,k_Size_m-1), (k_size_n - 1, k_size_n - 1)), mode='constant', constant_values=0)
    img_ZeroPadGray = Image.fromarray(img_ZeroPad_Arr)
    #img_ZeroPad.save("E:\Avinash\GRAD\dis\ECE558-Project2\\" + imgName + "_ZeroPad.png")
    #print("After zero padding",img_ZeroPadGray.size)
    
    ######## Zero Padding Implementation from Scratch ###############
    
    #################################################################
    
    return img_ZeroPadGray
    

def getWrapAroundImage(f, w):
    
    k_Size_m, k_size_n = w.shape; # get kernel Size
    m, n = f.size
    #print(k_Size_m)
    
    img_WrapAround_Arr = np.pad(f, ((k_Size_m-1,k_Size_m-1), (k_size_n - 1, k_size_n - 1), (0,0)), mode='wrap')
    img_WrapAround = Image.fromarray(img_WrapAround_Arr) 
    #print(img_WrapAround.size)
    #Image Size = 440 x 440
    #img_WrapAround.save("E:\Avinash\GRAD\dis\ECE558-Project1\\" + imgName + "_WrapAroundPad.png")
    
    ######## Wrap Around Implementation from Scratch ###############
    
    ################################################################
    
    return img_WrapAround


#generating gaussian kernel
def gaussian_kernel(sigma, size):
    mu = np.floor([size / 2, size / 2])
    size = int(size)
    kernel = np.zeros((size, size))
    
    for i in range(size):
        for j in range(size):
            kernel[i, j] = np.exp(-(0.5/(sigma*sigma)) * (np.square(i-mu[0]) + 
            np.square(j-mu[0]))) / np.sqrt(2*math.pi*sigma*sigma)

    kernel = kernel/np.sum(kernel)
    return kernel

def isGrayScale(input_image):
    flag = True;
    img_arr = np.asarray(input_image)
    l = len(img_arr.shape)
    if(l < 3):
        flag = False;
    return flag

def checkValidPyramidLevel(num_layers, inputSize):
    validL = False
    #Calculating if the number of layers is valid
    img_m , img_n = inputSize
    leastSide = 0
    #calculating the least side
    if(img_m >= img_n):
        leastSide = img_n
    else:
        leastSide = img_m
    
    #checking the maximum number of pyramid layers the image can have
    #print(leastSide)
    k = int(math.log2(leastSide))
    #print(k)
    if(num_layers <= k-2):
        validL = num_layers
    else:
        validL = k-2
    return validL
    

def getConvolvedImageGray(f, w):
    m,n = f.size
    kernel_m, kernel_n = w.shape
 
    pixel = f.load()
   
    kernel = w
    #print(m ,n)
    #print(kernel_m, kernel_n)

    ########### Creating a temporary Image to overwrite later on #####################
    img_temp_arr = np.zeros([n-(kernel_m-1), m-(kernel_n-1)], dtype=np.uint8)
    img_temp_arr[:] = [255]
    img_tmp_gray = Image.fromarray(img_temp_arr)
    pix = img_tmp_gray.load()
    #print(img_temp_arr.shape)
    #print("Temp :",img_tmp_gray.size)
    temp_m, temp_n = img_tmp_gray.size
    
    img_remove_pad_arr = np.zeros([m - kernel_m - 1, n - kernel_n - 1], dtype=np.uint8)
    img_remove_pad_arr[:] = [255]
    img_remove_pad = Image.fromarray(img_remove_pad_arr)
    pix_temp = img_remove_pad.load()
    m1, n1 = img_remove_pad.size
    start_index_m = temp_m - (m - kernel_m - 1)
    start_index_n = temp_n - (n - kernel_n - 1)
    #print("Start index", start_index_m, start_index_n)
    ##################################################################################
    
   
    #Creating separate matrices for R, G, B
    temp_arr = np.zeros([m,n], dtype=int)
    #print(temp_arrR.shape)
    #temp_arrG = np.zeros([m,n], dtype=int)
    #temp_arrB = np.zeros([m,n], dtype=int)
    for i in range(m):

        for j in range(n):
                coordinates = i,j
                val = f.getpixel(coordinates)
                temp_arr[i][j] = val
                #temp_arrG[i][j] = g
                #temp_arrB[i][j] = b
    
    #print(temp_arrR[0:3,0:3])
       
    #convolving for R,G and B separately then putting the, into a blank image created above
    temp_arr_conv = np.zeros([m-1,n-1], dtype=int)
    #temp_arrG_conv = np.zeros([m-1,n-1], dtype=int)
    #temp_arrB_conv = np.zeros([m-1,n-1], dtype=int)
    for i in range(m-kernel_n+1):
        for j in range(n-kernel_m+1):
            #print("aa")
            Gray = np.multiply(np.array(temp_arr[i:i+kernel_m, j:j+kernel_n]),np.array(kernel))
            #G = np.multiply(np.array(temp_arrG[i:i+kernel_m, j:j+kernel_n]),np.array(kernel))
            #B = np.multiply(np.array(temp_arrB[i:i+kernel_m, j:j+kernel_n]),np.array(kernel))
            #temp_arrR_conv[i][j] = np.sum(R)
            #print(i,j)
            #pix[i,j] = (int(np.sum(R)), int(np.sum(G)), int(np.sum(B)))
            #pix[i,j] = int(np.sum(Gray))
            img_tmp_gray.putpixel((i,j),int(np.sum(Gray)))
    
    ##Remove Extra Padding from the convolved image
    box = (start_index_m , start_index_n  , (m - kernel_m - 1) + 1 , (n - kernel_n - 1) + 1)
    img_remove = img_tmp_gray.crop(box)
    #print(img_remove.size)
    img_remove_m, img_remove_n = img_remove.size
    
    
    return img_remove




def getConvolvedImageMixed(f, w):
    m,n = f.size
    kernel_m1, kernel_n1 = w.shape
 
    pixel = f.load()
   
    kernel = w
    print(m ,n)
    print(kernel_m1, kernel_n1)

    ########### Creating a temporary Image to overwrite later on #####################
    img_temp_arr = np.zeros([n-(kernel_m1-1), m-(kernel_n1-1), 3], dtype=np.uint8)
    img_temp_arr[:,:] = [255, 255, 255]
    img_tmp = Image.fromarray(img_temp_arr)
    pix = img_tmp.load()
    #print(img_temp_arr.shape)
    #print("Temp :",img_tmp.size)
    temp_m, temp_n = img_tmp.size
    
    img_remove_pad_arr = np.zeros([m - kernel_m1 - 1, n - kernel_n1 - 1, 3], dtype=np.uint8)
    img_remove_pad_arr[:,:] = [255, 255, 255]
    img_remove_pad = Image.fromarray(img_remove_pad_arr)
    pix_temp = img_remove_pad.load()
    m1, n1 = img_remove_pad.size
    start_index_m = temp_m - (m - kernel_m1 - 1)
    start_index_n = temp_n - (n - kernel_n1 - 1)
    #print("Start index", start_index_m, start_index_n)
    ##################################################################################
    
   
    #Creating separate matrices for R, G, B
    temp_arrR = np.zeros([m,n], dtype=int)
    #print(temp_arrR.shape)
    temp_arrG = np.zeros([m,n], dtype=int)
    temp_arrB = np.zeros([m,n], dtype=int)
    for i in range(m):

        for j in range(n):
                coordinates = i,j
                r, g, b = f.getpixel(coordinates)
                temp_arrR[i][j] = r
                temp_arrG[i][j] = g
                temp_arrB[i][j] = b
    
    #print(temp_arrR[0:3,0:3])
       
    #convolving for R,G and B separately then putting the, into a blank image created above
    temp_arrR_conv = np.zeros([m-1,n-1], dtype=int)
    temp_arrG_conv = np.zeros([m-1,n-1], dtype=int)
    temp_arrB_conv = np.zeros([m-1,n-1], dtype=int)
    print("Kernel Dim :", kernel_m1)
    kernel_m1 = 240
    for i1 in range(0,m-kernel_n1+1):
        for j1 in range(0,n-kernel_m1+1):
            print("index I, J: ", i1,j1)
            R = np.multiply(np.array(temp_arrR[i1:i1+kernel_m1, j1:j1+kernel_n1]),np.array(kernel))
            G = np.multiply(np.array(temp_arrG[i1:i1+kernel_m1, j1:j1+kernel_n1]),np.array(kernel))
            B = np.multiply(np.array(temp_arrB[i1:i1+kernel_m1, j1:j1+kernel_n1]),np.array(kernel))
            #temp_arrR_conv[i][j] = np.sum(R)
            #print(i,j)
            pix[i1,j1] = (int(np.sum(R)), int(np.sum(G)), int(np.sum(B)))
            
    
    ##Remove Extra Padding from the convolved image
    box = (start_index_m , start_index_n  , (m - kernel_m1 - 1) + 1 , (n - kernel_n1 - 1) + 1)
    img_remove = img_tmp.crop(box)
    #print(img_remove.size)
    img_remove_m, img_remove_n = img_remove.size
    
    
    return img_remove






def getConvolvedImage(f, w):
    m,n = f.size
    kernel_m1, kernel_n1 = w.shape
 
    pixel = f.load()
   
    kernel = w
    print(m ,n)
    print(kernel_m1, kernel_n1)

    ########### Creating a temporary Image to overwrite later on #####################
    img_temp_arr = np.zeros([n-(kernel_m1-1), m-(kernel_n1-1), 3], dtype=np.uint8)
    img_temp_arr[:,:] = [255, 255, 255]
    img_tmp = Image.fromarray(img_temp_arr)
    pix = img_tmp.load()
    #print(img_temp_arr.shape)
    #print("Temp :",img_tmp.size)
    temp_m, temp_n = img_tmp.size
    
    img_remove_pad_arr = np.zeros([m - kernel_m1 - 1, n - kernel_n1 - 1, 3], dtype=np.uint8)
    img_remove_pad_arr[:,:] = [255, 255, 255]
    img_remove_pad = Image.fromarray(img_remove_pad_arr)
    pix_temp = img_remove_pad.load()
    m1, n1 = img_remove_pad.size
    start_index_m = temp_m - (m - kernel_m1 - 1)
    start_index_n = temp_n - (n - kernel_n1 - 1)
    #print("Start index", start_index_m, start_index_n)
    ##################################################################################
    
   
    #Creating separate matrices for R, G, B
    temp_arrR = np.zeros([m,n], dtype=int)
    #print(temp_arrR.shape)
    temp_arrG = np.zeros([m,n], dtype=int)
    temp_arrB = np.zeros([m,n], dtype=int)
    for i in range(m):

        for j in range(n):
                coordinates = i,j
                r, g, b = f.getpixel(coordinates)
                temp_arrR[i][j] = r
                temp_arrG[i][j] = g
                temp_arrB[i][j] = b
    
    #print(temp_arrR[0:3,0:3])
       
    #convolving for R,G and B separately then putting the, into a blank image created above
    temp_arrR_conv = np.zeros([m-1,n-1], dtype=int)
    temp_arrG_conv = np.zeros([m-1,n-1], dtype=int)
    temp_arrB_conv = np.zeros([m-1,n-1], dtype=int)
    print("Kernel Dim :", kernel_m1)
    for i1 in range(0,m-kernel_n1+1):
        for j1 in range(0,n-kernel_m1+1):
            #print("index I: ", i1)
            R = np.multiply(np.array(temp_arrR[i1:i1+kernel_m1, j1:j1+kernel_n1]),np.array(kernel))
            G = np.multiply(np.array(temp_arrG[i1:i1+kernel_m1, j1:j1+kernel_n1]),np.array(kernel))
            B = np.multiply(np.array(temp_arrB[i1:i1+kernel_m1, j1:j1+kernel_n1]),np.array(kernel))
            #temp_arrR_conv[i][j] = np.sum(R)
            #print(i,j)
            pix[i1,j1] = (int(np.sum(R)), int(np.sum(G)), int(np.sum(B)))
            
    
    ##Remove Extra Padding from the convolved image
    box = (start_index_m , start_index_n  , (m - kernel_m1 - 1) + 1 , (n - kernel_n1 - 1) + 1)
    img_remove = img_tmp.crop(box)
    #print(img_remove.size)
    img_remove_m, img_remove_n = img_remove.size
    
    
    return img_remove


def flipkernel(w):
    
    flip_w = np.flipud(np.fliplr(w))
    print(flip_w)
    
    return flip_w


#subsample the convolved grayscale image
def SubSampleImageGray(Img):
    convImg_m, convImg_n = Img.size
    
    ImgPix = Img.load()
    
    ########### Creating a temporary Image ###############
    img_sample_pad_arr = np.zeros([int(convImg_n/2), int(convImg_m/2)], dtype=np.uint8)
    img_sample_pad_arr[:,:] = [255]
    img_sample_pad_gray = Image.fromarray(img_sample_pad_arr)
    pix_temp = img_sample_pad_gray.load()
    m1, n1 = img_sample_pad_gray.size
    #print("Sample Size", m1, n1)
    ##################################################################################
    
    
    for i in range(m1):
        for j in range(n1):
            #print(i, j)
            #pix_temp[i, j] = ImgPix[2*i, 2*j]
            img_sample_pad_gray.putpixel((i, j), ImgPix[2*i, 2*j])
            
    
    return img_sample_pad_gray


#subsample the convolved image
def SubSampleImage(Img):
    
    convImg_m, convImg_n = Img.size
    
    ImgPix = Img.load()
    
    ########### Creating a temporary Image ###############
    img_sample_pad_arr = np.zeros([int(convImg_n/2), int(convImg_m/2), 3], dtype=np.uint8)
    img_sample_pad_arr[:,:] = [255, 255, 255]
    img_sample_pad = Image.fromarray(img_sample_pad_arr)
    pix_temp = img_sample_pad.load()
    m1, n1 = img_sample_pad.size
    #print("Sample Size", m1, n1)
    ##################################################################################
    
    
    for i in range(m1):
        for j in range(n1):
            #print(i, j)
            pix_temp[i, j] = ImgPix[2*i, 2*j]
          
            
    
    return img_sample_pad

def ComputePyrGray(input_image, num_layers):
    
    window=5 #kernel size
    offset= window//2
    w =gaussian_kernel(1.4, window) #get the kernel
    
    #flip the kernel along both the axes
    flip_w = flipkernel(w)
    
    #get Zero padded image
    imgZeroPad = getZeroPaddedImageGrayScale(input_image, w)
    #imgWrapAround = getWrapAroundImage(input_image, w)
    #Perform Convolution
    convImg = getConvolvedImageGray(imgZeroPad, flip_w)
    #Sub sample the convolved image
    
    #for i in range(num_layers):
    sampledImg = SubSampleImageGray(convImg) 
    
    return sampledImg
    
    

def ComputePyr(input_image, num_layers):
    
    #check if image is RGB or Gray
    print(num_layers)
    window=5 #kernel size
    offset= window//2
    w =gaussian_kernel(1.4, window) #get the kernel
    
    #flip the kernel along both the axes
    flip_w = flipkernel(w)
    
    #get Zero padded image
    imgZeroPad = getZeroPaddedImage(input_image, w)
    #imgWrapAround = getWrapAroundImage(input_image, w)
    #Perform Convolution
    convImg = getConvolvedImage(imgZeroPad, flip_w)
    #Sub sample the convolved image
    
    #for i in range(num_layers):
    sampledImg = SubSampleImage(convImg) 
    #List for gaussian pyramid
    #sampledImage = conv2(input_image, gwindow)
    #sampledImg.save("Gaussian" + str(num_layers) + ".png")
    #gaussianpyramidList.append(sampledImg)

    #    gaussianpyramidList.append(sampledImg)
    #else:
    #    gaussianpyramidList.append(sampledImg)
    #    ComputePyr(sampledImg, num_layers - 1)
        
    return sampledImg
        #gaussianpyramidList.append(sampledImg)

        
def upSampleGaussianPyramid(img):
    
    upImg_m, upImg_n = img.size
    
    upImgPix = img.load()
    
    ########### Creating a temporary Image ###############
    img_upSample_arr = np.zeros([int(upImg_n*2), int(upImg_m*2), 3], dtype=np.uint8)
    img_upSample_arr[:,:] = [255, 255, 255]
    img_upSample = Image.fromarray(img_upSample_arr)
    pix_temp_upSamp = img_upSample.load()
    m1, n1 = img_upSample.size
    #print("Sample Size", m1, n1)
    ##################################################################################
    
    for i in range(upImg_m):
        for j in range(upImg_n):
            pix_temp_upSamp[2*i, 2*j] = upImgPix[i, j]
            pix_temp_upSamp[2*i, 2*j + 1] = upImgPix[i, j]
            pix_temp_upSamp[2*i + 1, 2*j] = upImgPix[i, j]
            pix_temp_upSamp[2*i + 1, 2*j + 1] = upImgPix[i, j]
            
    
    
    return img_upSample


def addImages(maskImg, maskInvImg):
    
    maskImg_m, maskImg_n = maskImg.size
    
    tempImgMaskPix = maskImg.load()
    tempImgMaskInvPix = maskInvImg.load()
    
    ########### Creating a temporary Image ###############
    img_tempmix_arr = np.zeros([int(maskImg_n), int(maskImg_m), 3], dtype=np.uint8)
    img_tempmix_arr[:,:] = [255, 255, 255]
    img_tempMix = Image.fromarray(img_tempmix_arr)
    pix_temp_mix = img_tempMix.load()
    m1, n1 = img_tempMix.size
    #print("Sample Size", m1, n1)
    ##################################################################################
    
    for i in range(maskImg_m):
        for j in range(maskImg_n):
            coordinates = i,j
            r, g, b = maskImg.getpixel(coordinates)
            r1, g1, b1 = maskInvImg.getpixel(coordinates)
            pix_temp_mix[i,j] = (r+r1, g+g1, b+b1)
            
    
    return img_tempMix
    
    
    
    
    

def multiplyMask(laplacianImg, mask):
    
    lapImg_m, lapImg_n = laplacianImg.size
    
    #tempimgPix = laplacianImg.load()
    
    ########### Creating a temporary Image ###############
    img_lapmask_arr = np.zeros([int(lapImg_n), int(lapImg_m), 3], dtype=np.uint8)
    img_lapmask_arr[:,:] = [255, 255, 255]
    img_lapMask = Image.fromarray(img_lapmask_arr)
    pix_temp_lapmask = img_lapMask.load()
    m1, n1 = img_lapMask.size
    #print("Sample Size", m1, n1)
    ##################################################################################
    
    for i in range(lapImg_m):
        for j in range(lapImg_n):
            coordinates = i,j
            r, g, b = laplacianImg.getpixel(coordinates)
            maskVal = mask.getpixel(coordinates)
            if(maskVal > 250):
                maskVal = 1
            else:
                maskVal = 0
            pix_temp_lapmask[i,j] = (r*maskVal, g*maskVal, b*maskVal)
            
    return img_lapMask
    
    

def computeLaplacian(gaussianImg, reconstructedImg):
    
    m, n = gaussianImg.size
    #print("Lap", m, n)
    
    ########### Creating a temporary Image ###############
    laplacian_arr = np.zeros([int(n), int(m), 3], dtype=np.uint8)
    laplacian_arr[:,:] = [255, 255, 255]
    laplacianImg = Image.fromarray(laplacian_arr)
    m1, n1 = laplacianImg.size
    pixLaplacian = laplacianImg.load()
    ##################################################################################
    
    gaussianPix = gaussianImg.load()
    reConstructedPix = reconstructedImg.load()
    #compute the difference in value of each channel to generate Laplacian
    for i in range(m1):
        for j in range(n1):
            rG, gG, bG = gaussianPix[i, j]
            rRec, gRec, bRec = reConstructedPix[i, j]
            pixLaplacian[i, j] = rG-rRec, gG-gRec, bG-bRec
            #pixLaplacian[i, j] = gaussianPix[i, j]-reConstructedPix[i, j]
    
    
    return laplacianImg



    
    
    
    

#imgName = input("Enter the Image name you want. Choose from the given options:\n1. lena\n2. Wolves")
#img = Image.open(imgName + ".png")
#Open Images 1. apai4, 2. mask, 3. John Wick, 4. mask Inverse
#created the masks in GUI and loading them here
apai4Img = Image.open("apai4.jpg")
apai4_mask = Image.open("apai4_mask.jpg")
johnWickImg = Image.open("johnWick.jpg")
apai4_maskInv = Image.open("apai4_maskInv.jpg")

#created laplacian and gaussian lists for region blending
apai4GaussianList = []
apai4LaplacianList = []
johnWickGaussianList = []
johnWickLapLacianList = []
apai4_maskGaussianList = []
apai4_maskInvGaussianList = []
apai4_johnWick_LaplacianList = []

#img = Image.open(imgName + '.jpg')

#img_copy = img.copy()
#gaussian Pyramid List with the original image
#gaussianpyramidList = [img_copy]
num_layer = input("Enter the number of layers for pyramid")
#grayScale = isGrayScale(img)
#m, n = img.size
m, n = apai4Img.size
img_size = (m,n)
#Check if has num_layers is a valid pyramid level if not getthe maximum
validLevel = checkValidPyramidLevel(int(num_layer), img_size)

################# Generating gaussian pyramids for the two images and the mask and mas inverse ##################
apai4GaussianList.append(apai4Img)
johnWickGaussianList.append(johnWickImg)
#get the gaussian pyramid for apai4img
apai4sampledImg = ComputePyr(apai4Img, validLevel)
apai4GaussianList.append(apai4sampledImg)
for i in range(validLevel-1):
    apai4sampledImg = ComputePyr(apai4sampledImg, validLevel)
    apai4GaussianList.append(apai4sampledImg)
    
## Save the gaussian pyramid images
i = 0
for img in apai4GaussianList:
    img.save("apai4Gaussian" + str(i) + ".png")
    i= i+1
    
#get the gaussian pyramid for Background image
johnWickSampledImg = ComputePyr(johnWickImg, validLevel)
johnWickGaussianList.append(johnWickSampledImg)
for i in range(validLevel-1):
    johnWickSampledImg = ComputePyr(johnWickSampledImg, validLevel)
    johnWickGaussianList.append(johnWickSampledImg)
## Save the gaussian pyramid images
i = 0
for img in johnWickGaussianList:
    img.save("johnWick" + str(i) + ".png")
    i= i+1
    
    
#create the gaussian list for mask
apai4_maskGaussianList.append(apai4_mask)
apai4MaskSampledImg = ComputePyrGray(apai4_mask, validLevel)
apai4_maskGaussianList.append(apai4MaskSampledImg)
for i in range(validLevel-1):
    apai4MaskSampledImg = ComputePyrGray(apai4MaskSampledImg, validLevel-1)
    apai4_maskGaussianList.append(apai4MaskSampledImg)
#save the gaussian pyramid for mask grayScale Image
i = 0
for img in apai4_maskGaussianList:
    img.save("mask" + str(i) + ".png")
    i= i+1

#create the gaussian pyramid for mask inverse
apai4_maskInvGaussianList.append(apai4_maskInv)
apai4MaskInvSampledImg = ComputePyrGray(apai4_maskInv, validLevel)
apai4_maskInvGaussianList.append(apai4MaskInvSampledImg)
for i in range(validLevel-1):
    apai4MaskInvSampledImg = ComputePyrGray(apai4MaskInvSampledImg, validLevel-1)
    apai4_maskInvGaussianList.append(apai4MaskInvSampledImg)

#save the gaussian pyramid for the mask inverse gray scale
i = 0
for img in apai4_maskInvGaussianList:
    img.save("maskInv" + str(i) + ".png")
    i= i+1
    
    
    
#####################################################################################
#get the gaussian for mask for foreground Image and maskInv for background image
#apai4_maskGaussianList = ComputePyr(apai4_mask, validLevel)
#apai4_maskInvGaussianList = ComputePyr(apai4_maskInv, validLevel)

#print("apai4 list size",len(apai4GaussianList))
#gPyr = ComputePyr(img, validLevel)
#print("Pyramid length",len(gPyr))

gaussianReconstructionList = []
laplacianList = []

########### Computing laplacian list for apai4 image ##############

L = len(apai4GaussianList)- 1

#upsampling the gaussian pyramid using nearest neighborhood interpolation
#The gaussian list has sub sampled images from original image to the last layer
#Ex : 0 to 5

for i in range(L, 0, -1):
    #get the reconstructed image using nearest neighboohood interpolation
    reConstructedImg = upSampleGaussianPyramid(apai4GaussianList[i])
    reConstructedImg.save("Reconstructed_apai" + str(i) + ".png")
    #Compute Laplacian by subtracting the reconstructed image from the gaussina pyramid
    laplacianImg = computeLaplacian(apai4GaussianList[i - 1], reConstructedImg)
    apai4LaplacianList.append(laplacianImg)
    #laplacianImg.save("apai4Laplacian" + str(i) + ".png")
# save the laplacian list
i = 0
for img in apai4LaplacianList:
    img.save("apai4Lap" + str(i) + ".png")
    i= i+1
###########################################################################    
    
#######  Computing laplacian list for Background image(John Wick) ##############
L = len(johnWickGaussianList)- 1

#upsampling the gaussian pyramid using nearest neighborhood interpolation
#The gaussian list has sub sampled images from original image to the last layer
#Ex : 0 to 5
for i in range(L, 0, -1):
    #get the reconstructed image using nearest neighboohood interpolation
    reConstructedImg = upSampleGaussianPyramid(johnWickGaussianList[i])
    #reConstructedImg.save("Reconstructed" + str(i) + ".png")
    #Compute Laplacian by subtracting the reconstructed image from the gaussina pyramid
    laplacianImg = computeLaplacian(johnWickGaussianList[i - 1], reConstructedImg)
    johnWickLapLacianList.append(laplacianImg)
    #laplacianImg.save("johnWick" + str(i) + ".png")    
# save the laplacian list
i = 0
for img in johnWickLapLacianList:
    img.save("johnWickLap" + str(i) + ".png")
    i= i+1
###########################################################################   
######### Creating the combined laplacian list using the mask #############
###########################################################################

L1 = len(apai4LaplacianList)

for i in range(L1):
    
    #multiplying the apai4 and mask and johnWick and mask Inverse
    apai4_maskMultImg = multiplyMask(apai4LaplacianList[i], apai4_maskGaussianList[L1-i-1])
    #apai4_maskMultImg.save("apai4_mask"+str(i)+".png")
    johnWick_maskMultImg = multiplyMask(johnWickLapLacianList[i], apai4_maskInvGaussianList[L1-i-1])
    
    mixedImg = addImages(apai4_maskMultImg, johnWick_maskMultImg)
    apai4_johnWick_LaplacianList.append(mixedImg)
    
    
#### save the mixed images
i=0
for img in apai4_johnWick_LaplacianList:
    img.save("mixed" + str(i) + ".png")
    i = i+1


## create the mixed image using convolution ####
reconstructed_apai4Img = upSampleGaussianPyramid(apai4GaussianList[L])
reconstructed_johnWickImg = upSampleGaussianPyramid(johnWickGaussianList[L])

apai4_maskFilter = flipkernel(np.array(apai4_maskGaussianList[L]))
apai4_maskInvFilter = flipkernel(np.array(apai4_maskInvGaussianList[L]))

apai4ZeroPadded = getZeroPaddedImage(reconstructed_apai4Img, apai4_maskFilter)
johnWickZeroPadded = getZeroPaddedImage(reconstructed_johnWickImg,apai4_maskInvFilter)

convolvedapai4Img = getConvolvedImageMixed(apai4ZeroPadded, apai4_maskFilter)
convolvedjohhnWickImg = getConvolvedImageMixed(johnWickZeroPadded, apai4_maskInvFilter)

convolvedapai4Img.save("convapai4.png")
convolvedjohhnWickImg.save("convolvedJohn.png")




Enter the number of layers for pyramid3
3
[[0.01214612 0.02610994 0.03369732 0.02610994 0.01214612]
 [0.02610994 0.0561273  0.07243752 0.0561273  0.02610994]
 [0.03369732 0.07243752 0.09348738 0.07243752 0.03369732]
 [0.02610994 0.0561273  0.07243752 0.0561273  0.02610994]
 [0.01214612 0.02610994 0.03369732 0.02610994 0.01214612]]
1088 1928
5 5
Kernel Dim : 5
3
[[0.01214612 0.02610994 0.03369732 0.02610994 0.01214612]
 [0.02610994 0.0561273  0.07243752 0.0561273  0.02610994]
 [0.03369732 0.07243752 0.09348738 0.07243752 0.03369732]
 [0.02610994 0.0561273  0.07243752 0.0561273  0.02610994]
 [0.01214612 0.02610994 0.03369732 0.02610994 0.01214612]]
548 968
5 5
Kernel Dim : 5
3
[[0.01214612 0.02610994 0.03369732 0.02610994 0.01214612]
 [0.02610994 0.0561273  0.07243752 0.0561273  0.02610994]
 [0.03369732 0.07243752 0.09348738 0.07243752 0.03369732]
 [0.02610994 0.0561273  0.07243752 0.0561273  0.02610994]
 [0.01214612 0.02610994 0.03369732 0.02610994 0.01214612]]
278 488
5 5
Kernel Dim : 

index I, J:  0 367
index I, J:  0 368
index I, J:  0 369
index I, J:  0 370
index I, J:  0 371
index I, J:  0 372
index I, J:  0 373
index I, J:  0 374
index I, J:  0 375
index I, J:  0 376
index I, J:  0 377
index I, J:  0 378
index I, J:  0 379
index I, J:  0 380
index I, J:  0 381
index I, J:  0 382
index I, J:  0 383
index I, J:  0 384
index I, J:  0 385
index I, J:  0 386
index I, J:  0 387
index I, J:  0 388
index I, J:  0 389
index I, J:  0 390
index I, J:  0 391
index I, J:  0 392
index I, J:  0 393
index I, J:  0 394
index I, J:  0 395
index I, J:  0 396
index I, J:  0 397
index I, J:  0 398
index I, J:  0 399
index I, J:  0 400
index I, J:  0 401
index I, J:  0 402
index I, J:  0 403
index I, J:  0 404
index I, J:  0 405
index I, J:  0 406
index I, J:  0 407
index I, J:  0 408
index I, J:  0 409
index I, J:  0 410
index I, J:  0 411
index I, J:  0 412
index I, J:  0 413
index I, J:  0 414
index I, J:  0 415
index I, J:  0 416
index I, J:  0 417
index I, J:  0 418
index I, J: 

index I, J:  1 393
index I, J:  1 394
index I, J:  1 395
index I, J:  1 396
index I, J:  1 397
index I, J:  1 398
index I, J:  1 399
index I, J:  1 400
index I, J:  1 401
index I, J:  1 402
index I, J:  1 403
index I, J:  1 404
index I, J:  1 405
index I, J:  1 406
index I, J:  1 407
index I, J:  1 408
index I, J:  1 409
index I, J:  1 410
index I, J:  1 411
index I, J:  1 412
index I, J:  1 413
index I, J:  1 414
index I, J:  1 415
index I, J:  1 416
index I, J:  1 417
index I, J:  1 418
index I, J:  1 419
index I, J:  1 420
index I, J:  1 421
index I, J:  1 422
index I, J:  1 423
index I, J:  1 424
index I, J:  1 425
index I, J:  1 426
index I, J:  1 427
index I, J:  1 428
index I, J:  1 429
index I, J:  1 430
index I, J:  1 431
index I, J:  1 432
index I, J:  1 433
index I, J:  1 434
index I, J:  1 435
index I, J:  1 436
index I, J:  1 437
index I, J:  1 438
index I, J:  1 439
index I, J:  1 440
index I, J:  1 441
index I, J:  1 442
index I, J:  1 443
index I, J:  1 444
index I, J: 

index I, J:  2 430
index I, J:  2 431
index I, J:  2 432
index I, J:  2 433
index I, J:  2 434
index I, J:  2 435
index I, J:  2 436
index I, J:  2 437
index I, J:  2 438
index I, J:  2 439
index I, J:  2 440
index I, J:  2 441
index I, J:  2 442
index I, J:  2 443
index I, J:  2 444
index I, J:  2 445
index I, J:  2 446
index I, J:  2 447
index I, J:  2 448
index I, J:  2 449
index I, J:  2 450
index I, J:  2 451
index I, J:  2 452
index I, J:  2 453
index I, J:  2 454
index I, J:  2 455
index I, J:  2 456
index I, J:  2 457
index I, J:  2 458
index I, J:  2 459
index I, J:  2 460
index I, J:  2 461
index I, J:  2 462
index I, J:  2 463
index I, J:  2 464
index I, J:  2 465
index I, J:  2 466
index I, J:  2 467
index I, J:  2 468
index I, J:  2 469
index I, J:  2 470
index I, J:  2 471
index I, J:  2 472
index I, J:  2 473
index I, J:  2 474
index I, J:  2 475
index I, J:  2 476
index I, J:  2 477
index I, J:  2 478
index I, J:  2 479
index I, J:  2 480
index I, J:  2 481
index I, J: 

index I, J:  3 462
index I, J:  3 463
index I, J:  3 464
index I, J:  3 465
index I, J:  3 466
index I, J:  3 467
index I, J:  3 468
index I, J:  3 469
index I, J:  3 470
index I, J:  3 471
index I, J:  3 472
index I, J:  3 473
index I, J:  3 474
index I, J:  3 475
index I, J:  3 476
index I, J:  3 477
index I, J:  3 478
index I, J:  3 479
index I, J:  3 480
index I, J:  3 481
index I, J:  3 482
index I, J:  3 483
index I, J:  3 484
index I, J:  3 485
index I, J:  3 486
index I, J:  3 487
index I, J:  3 488
index I, J:  3 489
index I, J:  3 490
index I, J:  3 491
index I, J:  3 492
index I, J:  3 493
index I, J:  3 494
index I, J:  3 495
index I, J:  3 496
index I, J:  3 497
index I, J:  3 498
index I, J:  3 499
index I, J:  3 500
index I, J:  3 501
index I, J:  3 502
index I, J:  3 503
index I, J:  3 504
index I, J:  3 505
index I, J:  3 506
index I, J:  3 507
index I, J:  3 508
index I, J:  3 509
index I, J:  3 510
index I, J:  3 511
index I, J:  3 512
index I, J:  3 513
index I, J: 

...

index I, J:  296 699
index I, J:  296 700
index I, J:  296 701
index I, J:  296 702
index I, J:  296 703
index I, J:  296 704
index I, J:  296 705
index I, J:  296 706
index I, J:  296 707
index I, J:  296 708
index I, J:  296 709
index I, J:  296 710
index I, J:  296 711
index I, J:  296 712
index I, J:  296 713
index I, J:  296 714
index I, J:  296 715
index I, J:  296 716
index I, J:  296 717
index I, J:  296 718
index I, J:  297 0
index I, J:  297 1
index I, J:  297 2
index I, J:  297 3
index I, J:  297 4
index I, J:  297 5
index I, J:  297 6
index I, J:  297 7
index I, J:  297 8
index I, J:  297 9
index I, J:  297 10
index I, J:  297 11
index I, J:  297 12
index I, J:  297 13
index I, J:  297 14
index I, J:  297 15
index I, J:  297 16
index I, J:  297 17
index I, J:  297 18
index I, J:  297 19
index I, J:  297 20
index I, J:  297 21
index I, J:  297 22
index I, J:  297 23
index I, J:  297 24
index I, J:  297 25
index I, J:  297 26
index I, J:  297 27
index I, J:  297 28
index I, J

index I, J:  297 459
index I, J:  297 460
index I, J:  297 461
index I, J:  297 462
index I, J:  297 463
index I, J:  297 464
index I, J:  297 465
index I, J:  297 466
index I, J:  297 467
index I, J:  297 468
index I, J:  297 469
index I, J:  297 470
index I, J:  297 471
index I, J:  297 472
index I, J:  297 473
index I, J:  297 474
index I, J:  297 475
index I, J:  297 476
index I, J:  297 477
index I, J:  297 478
index I, J:  297 479
index I, J:  297 480
index I, J:  297 481
index I, J:  297 482
index I, J:  297 483
index I, J:  297 484
index I, J:  297 485
index I, J:  297 486
index I, J:  297 487
index I, J:  297 488
index I, J:  297 489
index I, J:  297 490
index I, J:  297 491
index I, J:  297 492
index I, J:  297 493
index I, J:  297 494
index I, J:  297 495
index I, J:  297 496
index I, J:  297 497
index I, J:  297 498
index I, J:  297 499
index I, J:  297 500
index I, J:  297 501
index I, J:  297 502
index I, J:  297 503
index I, J:  297 504
index I, J:  297 505
index I, J:  

index I, J:  298 222
index I, J:  298 223
index I, J:  298 224
index I, J:  298 225
index I, J:  298 226
index I, J:  298 227
index I, J:  298 228
index I, J:  298 229
index I, J:  298 230
index I, J:  298 231
index I, J:  298 232
index I, J:  298 233
index I, J:  298 234
index I, J:  298 235
index I, J:  298 236
index I, J:  298 237
index I, J:  298 238
index I, J:  298 239
index I, J:  298 240
index I, J:  298 241
index I, J:  298 242
index I, J:  298 243
index I, J:  298 244
index I, J:  298 245
index I, J:  298 246
index I, J:  298 247
index I, J:  298 248
index I, J:  298 249
index I, J:  298 250
index I, J:  298 251
index I, J:  298 252
index I, J:  298 253
index I, J:  298 254
index I, J:  298 255
index I, J:  298 256
index I, J:  298 257
index I, J:  298 258
index I, J:  298 259
index I, J:  298 260
index I, J:  298 261
index I, J:  298 262
index I, J:  298 263
index I, J:  298 264
index I, J:  298 265
index I, J:  298 266
index I, J:  298 267
index I, J:  298 268
index I, J:  

index I, J:  298 699
index I, J:  298 700
index I, J:  298 701
index I, J:  298 702
index I, J:  298 703
index I, J:  298 704
index I, J:  298 705
index I, J:  298 706
index I, J:  298 707
index I, J:  298 708
index I, J:  298 709
index I, J:  298 710
index I, J:  298 711
index I, J:  298 712
index I, J:  298 713
index I, J:  298 714
index I, J:  298 715
index I, J:  298 716
index I, J:  298 717
index I, J:  298 718
index I, J:  299 0


ValueError: operands could not be broadcast together with shapes (239,135) (240,135) 

In [ ]:
import cv2

img = cv2.imread("lena_mask.png")
ret, thresh1 = cv2.threshold(img, 254, 255, cv2.THRESH_BINARY)

cv2.imwrite("lena_thresh.png", thresh1)